# set env

In [2]:
# Common imports
import sys
import os
import time
import datetime
from datetime import timedelta, timezone, date

import shutil
import math
import json
import requests
from urllib import request, parse
import numpy as np
import pandas as pd
import seaborn as sns
import shortuuid

# Matplotlib settings
import matplotlib.pyplot as plt

%matplotlib notebook

plt.rcParams['font.sans-serif'] = ['SimHei']  # 正常显示中文标签
plt.rcParams['axes.unicode_minus'] = False
plt.rcParams['axes.labelsize'] = 12
plt.rcParams['xtick.labelsize'] = 10
plt.rcParams['ytick.labelsize'] = 10

# funcs

In [3]:
def datedelta(steps=1):
    """ 获取与当前日期间隔任意天数的日期 """
    today = datetime.date.today()
    steps = datetime.timedelta(days=steps)
    passdate = today-steps
    return str(passdate)

In [4]:
def get_utc8_tsp():
    """ 获取东八区时间戳 """
    utc_dt = datetime.datetime.utcnow().replace(tzinfo=timezone.utc)
    bj_dt = utc_dt.astimezone(timezone(timedelta(hours=8)))
    return str(int(datetime.datetime.timestamp(bj_dt)))

In [5]:
def load_token(json_token):
    with open(json_token, 'r', encoding='utf-8') as f:
        auth_code_dict = json.load(f)
    return auth_code_dict

In [6]:
def http_headers():
    headers = {
        "Content-Type": "application/json",
    }
    return headers

In [7]:
def ocpcbid_data(act_name, act_id, plttype, rsp_data, csv_file):
    names = ['targetPackageId', 'targetPackageName', 'ocpcBidType', 'equipmentType',
             'ocpcBid', 'ecpcMaxBidRatio', 'ecpcMinBidRatio', 'ocpcStage', 'scope']
    
    if rsp_data['header']['desc'] != 'success':
        return "Error: the response header's desc not success! "
    if not rsp_data['body']['data']:
        return "Error: no data, check the account is enable!"
    
    df = pd.DataFrame(rsp_data['body']['data'])
    df = df[names]
    df['account_name'] = act_name
    df['account_id'] = act_id
    df['platform'] = plttype
    df['dt'] = datedelta(0)
    df.to_csv(csv_file, sep='\t', index=None, header=None, mode='a')

In [8]:
def package_scope(act_name, act_id, plttype, rsp_data, csv_file):
    names = ['targetPackageId', 'scope']
    
    if rsp_data['header']['desc'] != 'success':
        return "Error: the response header's desc not success! "
    if not rsp_data['body']['data']:
        return "Error: no data, check the account is enable!"
    
    df = pd.DataFrame(rsp_data['body']['data'])
    df = df[names]
    df = df.dropna(how='any')
    df['scopedf'] = df.scope.map(lambda x: pd.DataFrame(x))
    
    for pid, subdf in zip(df.targetPackageId, df.scopedf):
        subdf['targetPackageId'] = pid
        
    fulldf = pd.concat(list(df.scopedf), ignore_index=True)
    
    fulldf['account_name'] = act_name
    fulldf['account_id'] = act_id
    fulldf['platform'] = plttype
    fulldf['dt'] = datedelta(0)
    fulldf = fulldf.drop_duplicates()  # 数据去重
    fulldf.to_csv(csv_file, sep='\t', index=None, header=None, mode='a')

In [9]:
def process_ocpcbid_data(src_csv):
    pcwap_rpt = os.path.join(data_path, 'baidu_sem_pcwap_ocpcbid_{}.xlsx'.format(datedelta(0)))
    bjapp_rpt = os.path.join(data_path, 'baidu_sem_bjapp_ocpcbid_{}.xlsx'.format(datedelta(0)))
    columns = ['投放包id', '投放包名称', '出价类型(1: ocpc 2: ecpc)', '优化的设备类型(1: PC 2: 移动)',
               '目标转化成本 (元/转化)', 'eCPC最大议价系数', 'eCPC最小议价系数', '投放阶段', '生效范围',
               '账户名称', '账户id', '平台类型', '日期']
    
    df = pd.read_csv(src_csv, sep='\t', names=columns)
    if 'pcwap' in src_csv:
        df.to_excel(pcwap_rpt, index=None)
    else:
        df.to_excel(bjapp_rpt, index=None)

In [10]:
def process_package_scope(src_csv):
    pcwap_rpt = os.path.join(data_path, 'baidu_sem_pcwap_package_scope_{}.xlsx'.format(datedelta(0)))
    bjapp_rpt = os.path.join(data_path, 'baidu_sem_bjapp_package_scope_{}.xlsx'.format(datedelta(0)))
    columns = ['计划id', '级别', '投放包id', '账户名称', '账户id', '平台类型', '日期']
    
    df = pd.read_csv(src_csv, sep='\t', names=columns)
    if 'pcwap' in src_csv:
        df.to_excel(pcwap_rpt, index=None)
    else:
        df.to_excel(bjapp_rpt, index=None)

# config

In [33]:
adgrps_url = 'https://api.e.qq.com/v1.1/adgroups/get'
pcwap_bid_csv = 'tencent_gdt_pcwap_bid_{}.csv'.format(datedelta(0))
bjapp_bid_csv = 'tencent_gdt_bjapp_bid_{}.csv'.format(datedelta(0))

# data_path = r'C:/Users/jsynl/JupyterFiles/channel_API/tencent_gdt/data'
# code_path = r'C:/Users/jsynl/JupyterFiles/channel_API/tencent_gdt/code'
# conf_path = r'C:/Users/jsynl/JupyterFiles/channel_API/tencent_gdt/conf'
data_path = r'/Users/jia/JupyterFiles/channel_API/tencent_gdt/data'
code_path = r'/Users/jia/JupyterFiles/channel_API/tencent_gdt/code'
conf_path = r'/Users/jia/JupyterFiles/channel_API/tencent_gdt/conf'

# authcode_file = r'C:/Users/jsynl/JupyterFiles/channel_API/tencent_gdt/conf/tencent_gdt_authcode.json'
authcode_file = r'/Users/jia/JupyterFiles/channel_API/tencent_gdt/conf/tencent_gdt_authcode.json'

In [43]:
authcodes = load_token(authcode_file)
# print('authcodes: \n', authcodes)

for account in authcodes.keys():
    account_id = authcodes[account]['account_id']
    refresh_token = authcodes[account]['refresh_token']
    
    access_token = update_ak(refresh_token)
    
    print('account: {}\n account_id: {}\n refresh_token: {}\n access_token: {}'.format(
        account, account_id, refresh_token, access_token))
    # page_num = 1

account: 广点通_安卓_品众1(2063261)
 account_id: 2063261
 refresh_token: b3ab44a545f17d15446133226755c76f
 access_token: 2e498e77c46c7f68252970a546063624
account: 广点通_安卓_品众2(15015458)
 account_id: 15015458
 refresh_token: 82415fcf192f192789cdc4fa8242c175
 access_token: 2c5efdb59f8369f79b2ec467f137655f
account: 广点通_安卓_品众3(15128620)
 account_id: 15128620
 refresh_token: d159607df13f9b983ce06e3d7fa9ba40
 access_token: a89d9b9d4ef0c4de333b57f8b2d78d51
account: 广点通_安卓_品众4(15128611)
 account_id: 15128611
 refresh_token: a7fe147a28c6424708f6eba5b66f5764
 access_token: ec7ae14819817b008bf8abcd36d33cb6
account: 广点通_安卓_品众5(15415282)
 account_id: 15415282
 refresh_token: 1240789bb27c008bf1f9a0be7a894c80
 access_token: 0f9cdc0744ef4a4b28abb2f217f55579
account: 广点通_安卓_品众6(15415253)
 account_id: 15415253
 refresh_token: 61e96893816036b00559c14c3d439c76
 access_token: 85c2f71bc20bcc7ffd7732c33c3def85
account: 广点通_安卓_品众7(17649585)
 account_id: 17649585
 refresh_token: bb767ecfd31daeab7a9d3c3a3151ab7b
 access

# 请求广告组数据

In [27]:
def update_ak(refresh_token):
    ''' 更新 access_token
        access_token 有效期为24小时，因此需要每24小时更新一次
        refresh_token 有效期为30天，每次更新 access_token 时 refresh_token 会自动续期
    '''
    token_url = 'https://api.e.qq.com/oauth/token'
    data = {
        'client_id': '1107590516',
        'client_secret': 'NbURQN2TxtdLbOAR',
        'grant_type': 'refresh_token',
        'refresh_token': refresh_token
        }
    try:
        response = requests.get(url=token_url, params=data)
        response.raise_for_status()
        # print(response.text)
        return json.loads(response.text)['data']['access_token']
    except Exception as e:
        print('Can not get access_token, raise an exception: \n', e)
        input()
        sys.exit()

In [25]:
def general_parameters(access_token, timestamp=None, nonce=None):
    # timestamp = get_utc8_tsp()
    # nonce = shortuuid.uuid(name=str(time.time()), pad_length=22) # 每次请求唯一标识，不能重复
    
    data = {'access_token': access_token,
            'timestamp': timestamp,
            'nonce': nonce,
            # 'fields': []
           }
    return data

In [26]:
def adgrps_parameters(account_id, page=1, is_deleted='false'):
    data = {
        'account_id': account_id
        ,'fields': ['campaign_id','adgroup_id','adgroup_name','bid_amount','daily_budget']
        ,'page': page
        ,'page_size': 100
        ,'is_deleted': is_deleted
        # ,'filtering': [{"field":"adgroup_name","operator":"CONTAINS","values":["广告"]}]
    }
    return data

In [16]:
def payload_parameters(access_token, account_id, page=1):
    gen_args = general_parameters(access_token)  # 全局（通用）请求参数
    adgrps_http_data = adgrps_parameters(account_id, page)
    
    adgrps_http_data.update(gen_args)
    
    for k in adgrps_http_data:
        if type(adgrps_http_data[k]) is not str:
            adgrps_http_data[k] = json.dumps(adgrps_http_data[k])
    return adgrps_http_data

In [17]:
def request_data(url, headers, data):
    """ 一个数据生成器 """
    
    try:        
        data['timestamp'] = get_utc8_tsp()
        data['nonce'] = shortuuid.uuid(name=str(time.time()), pad_length=22) # 每次请求唯一标识，不能重复
        
        resp = requests.get(url=url, params=data, headers=headers, timeout=60)
        
        if not resp.status_code == 200:
            return "Error: Unexpected response {}".format(resp)
        
        total_page = json.loads(resp.text)['data']['page_info']['total_page']
        print('total_page: ', total_page)

    except requests.exceptions.RequestException as e:
        # A serious problem happened, like an SSLError or InvalidURL
        return "Error: {}".format(e)
        
    while int(data['page']) <= int(total_page):
        # yield pd.DataFrame(json.loads(resp.text)['data'])
        yield json.loads(resp.text)
        
        data['page'] = int(data['page']) + 1
        data['timestamp'] = get_utc8_tsp()
        data['nonce'] = shortuuid.uuid(name=str(time.time()), pad_length=22) # 每次请求唯一标识，不能重复
        
        resp = requests.get(url=url, params=data, headers=headers, timeout=60)
        
    return 'All data has been returned!'

In [30]:
def adgrps_bid_data(act_name, act_id, rsp_data, csv_file):
    
    if not rsp_data['data']['list']:
        return "Error: no data, check the account is enable!"
    
    df = pd.DataFrame(rsp_data['data']['list'])
    df['account_name'] = act_name
    df['account_id'] = act_id
    # df['platform'] = plttype
    df['dt'] = datedelta(0)
    df.to_csv(csv_file, sep='\t', index=None, mode='a')

---

In [35]:
os.chdir(data_path)

authcodes = load_token(authcode_file)
# print('authcodes: \n', authcodes)

headers = http_headers()

for account in authcodes.keys():
    # if account != '广点通_安卓_品众3(15128620)':
        # continue
        
    refresh_token = authcodes[account]['refresh_token']
    
    account_id = authcodes[account]['account_id']
    access_token = update_ak(refresh_token)
    
    print('-- 拉取账户: {}'.format(account))
    
    http_data = payload_parameters(access_token, account_id, page=1)

    r = request_data(adgrps_url, headers, http_data)
    
    for content in r:
        # print(content)
        adgrps_bid_data(account, account_id, content, bjapp_bid_csv)
    


total_page:  67
{'data': {'list': [{'campaign_id': 134871422, 'adgroup_id': 281806099, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-定向包-交通类2-0212-车降价23-文案1-实惠好车（不带热区）-812--单出价-下单', 'bid_amount': 1434, 'daily_budget': 0}, {'campaign_id': 134793471, 'adgroup_id': 281747033, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-定向包-交通类2-0212-车降价23-文案1-实惠好车（不带热区）-811--单出价-下单', 'bid_amount': 1434, 'daily_budget': 0}, {'campaign_id': 134793337, 'adgroup_id': 281747017, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-定向包-交通类2-0212-车降价22-文案1-实惠好车（不带热区）-811--单出价-下单', 'bid_amount': 1524, 'daily_budget': 0}, {'campaign_id': 134793222, 'adgroup_id': 281747005, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-定向包-交通类2-0212-车降价21-文案1-实惠好车（不带热区）-811--单出价-下单', 'bid_amount': 1625, 'daily_budget': 0}, {'campaign_id': 134793098, 'adgroup_id': 281746981, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-定向包-交通类2-0212-车降价20-文案1-实惠好车（不带热区）-811--单出价-下单', 'bid_amount': 1225, 'daily_budget': 0}, {'campaign_id': 134793002, 'adgroup_id': 281746963, 'adgroup

{'data': {'list': [{'campaign_id': 132567362, 'adgroup_id': 279566714, 'adgroup_name': '报价安卓-c250-应用宝-系统推荐-logo-应用宝文案4-无-0806-4', 'bid_amount': 250, 'daily_budget': 0}, {'campaign_id': 132559356, 'adgroup_id': 279558418, 'adgroup_name': '报价安卓-c250-应用宝-系统推荐-logo-应用宝文案4-无-0806-3', 'bid_amount': 250, 'daily_budget': 0}, {'campaign_id': 132528642, 'adgroup_id': 279523911, 'adgroup_name': '报价安卓-c250-应用宝-系统推荐-logo-应用宝文案4-无-0806-11', 'bid_amount': 210, 'daily_budget': 0}, {'campaign_id': 132523765, 'adgroup_id': 279518599, 'adgroup_name': '报价安卓-c250-应用宝-系统推荐-logo-应用宝文案4-无-0806-10', 'bid_amount': 250, 'daily_budget': 0}, {'campaign_id': 132521804, 'adgroup_id': 279515819, 'adgroup_name': '报价安卓-c250-应用宝-系统推荐-logo-应用宝文案4-无-0806-9', 'bid_amount': 250, 'daily_budget': 0}, {'campaign_id': 132517409, 'adgroup_id': 279510028, 'adgroup_name': '报价安卓-c250-应用宝-系统推荐-logo-应用宝文案4-无-0806-8', 'bid_amount': 250, 'daily_budget': 0}, {'campaign_id': 132496564, 'adgroup_id': 279481870, 'adgroup_name': '报价安卓-c250-

{'data': {'list': [{'campaign_id': 110596303, 'adgroup_id': 244987059, 'adgroup_name': '报价安卓-c250-应用宝视频-汽车相关-实拍02-应用宝视频-无-0519_04', 'bid_amount': 320, 'daily_budget': 0}, {'campaign_id': 110596303, 'adgroup_id': 244987058, 'adgroup_name': '报价安卓-c250-应用宝视频-汽车相关-实拍02-应用宝视频-无-0519_03', 'bid_amount': 320, 'daily_budget': 0}, {'campaign_id': 110596303, 'adgroup_id': 244987057, 'adgroup_name': '报价安卓-c250-应用宝视频-汽车相关-实拍02-应用宝视频-无-0519_02', 'bid_amount': 320, 'daily_budget': 0}, {'campaign_id': 110596303, 'adgroup_id': 244987056, 'adgroup_name': '报价安卓-c250-应用宝视频-汽车相关-实拍02-应用宝视频-无-0519_01', 'bid_amount': 320, 'daily_budget': 0}, {'campaign_id': 110596303, 'adgroup_id': 244985956, 'adgroup_name': '报价安卓-c250-应用宝视频-汽车相关-实拍01-应用宝视频-无-0519_04', 'bid_amount': 320, 'daily_budget': 0}, {'campaign_id': 110596303, 'adgroup_id': 244985955, 'adgroup_name': '报价安卓-c250-应用宝视频-汽车相关-实拍01-应用宝视频-无-0519_03', 'bid_amount': 320, 'daily_budget': 0}, {'campaign_id': 110596303, 'adgroup_id': 244985953, 'adgroup_name': '

{'data': {'list': [{'campaign_id': 106646087, 'adgroup_id': 237341936, 'adgroup_name': '报价安卓-c250-XS通栏大图960X274-交通类2-多车01-文案1-实惠好车无热区-0430-两阶段-下单', 'bid_amount': 1300, 'daily_budget': 0}, {'campaign_id': 99301629, 'adgroup_id': 236995235, 'adgroup_name': '报价安卓-c250-应用宝-运动健康旅游1-logo-应用宝文案3-无-0326-1-副本', 'bid_amount': 200, 'daily_budget': 0}, {'campaign_id': 105140623, 'adgroup_id': 236982161, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-交通类2-多车05-文案1-实惠好车-0429-1-两阶段-下单', 'bid_amount': 1300, 'daily_budget': 0}, {'campaign_id': 105140623, 'adgroup_id': 236981196, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-交通类2-多车04-文案1-实惠好车-0429-1-两阶段-下单', 'bid_amount': 1300, 'daily_budget': 0}, {'campaign_id': 105140623, 'adgroup_id': 236980148, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-交通类2-多车03-文案1-实惠好车-0429-1-两阶段-下单', 'bid_amount': 1300, 'daily_budget': 0}, {'campaign_id': 105140623, 'adgroup_id': 236979344, 'adgroup_name': '报价安卓-c250-XQ大图1280x720-交通类2-多车02-文案1-实惠好车-0429-1-两阶段-下单', 'bid_amount': 1300, 'daily_bu

{'data': {'list': [{'campaign_id': 93213404, 'adgroup_id': 228870280, 'adgroup_name': '报价安卓-c250-XQ小图480x320-交通类2男-小图8-文案2-实惠好车-0409-1-副本', 'bid_amount': 900, 'daily_budget': 0}, {'campaign_id': 102209573, 'adgroup_id': 228693998, 'adgroup_name': '报价安卓-c250-腾讯新闻大图1280x720-交通类2-动态创意-直降文案1-实惠好车（无热区）-0409-1-双出价-下单', 'bid_amount': 900, 'daily_budget': 0}, {'campaign_id': 102203914, 'adgroup_id': 228683756, 'adgroup_name': '报价安卓-c250-腾讯新闻小图480x320-交通类2-动态创意-直降文案1-实惠好车（无热区）-0409-1-双出价-下单', 'bid_amount': 900, 'daily_budget': 0}, {'campaign_id': 101927942, 'adgroup_id': 228205967, 'adgroup_name': '报价安卓-c250-应用宝-交通类汽车词-logo-应用宝文案4-无-0408-1', 'bid_amount': 200, 'daily_budget': 0}, {'campaign_id': 98591424, 'adgroup_id': 227713667, 'adgroup_name': '报价安卓-c250-腾讯新闻小图480x320-交通类2-动态创意-直降文案1-实惠好车-0407-1-副本', 'bid_amount': 900, 'daily_budget': 0}, {'campaign_id': 97155226, 'adgroup_id': 227045955, 'adgroup_name': '报价安卓-c250-XQ小图480x320-交通类2-小图4-文案1-实惠好车（无热区）-0404-1-双出价-留存-副本', 'bid_amount': 900, 'dail

...

{'data': {'list': [{'campaign_id': 168868285, 'adgroup_id': 346764402, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量-23', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346764398, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量-19_03_04_02_04_03', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346764388, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量-19_03_04_02_04_02', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346764373, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量-19_03_04_02_04_01', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346763590, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量-19_03_04_02_04', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 16886828

{'data': {'list': [{'campaign_id': 168868285, 'adgroup_id': 346712350, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量_6', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346712337, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量_02_03_03', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346712323, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量_02_03_02', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346712311, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量_02_03_01', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346710571, 'adgroup_name': '报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-1209-亦复-双出价-下单-优先拿量_02_04', 'bid_amount': 3110, 'daily_budget': 0}, {'campaign_id': 168868285, 'adgroup_id': 346710559, 'adgroup_

{'data': {'list': [{'campaign_id': 166240133, 'adgroup_id': 340177677, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-男通投-动态创意-优质跑量-询价-销量询价（有热区）-1126-亦复-双出价-下单-优先拿量-3192', 'bid_amount': 2866, 'daily_budget': 0}, {'campaign_id': 166240133, 'adgroup_id': 340175242, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-男通投-动态创意-优质跑量-询价-销量询价（有热区）-1126-亦复-双出价-下单-优先拿量-3191', 'bid_amount': 2866, 'daily_budget': 0}, {'campaign_id': 166159457, 'adgroup_id': 339995755, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-美女上车-询价-销量询价（有热区）-1126-亦复-双出价-下单-优先拿量-3190', 'bid_amount': 2866, 'daily_budget': 0}, {'campaign_id': 166159457, 'adgroup_id': 339993604, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-美女上车-询价-销量询价（有热区）-1126-亦复-双出价-下单-优先拿量-3177', 'bid_amount': 2522, 'daily_budget': 0}, {'campaign_id': 165970853, 'adgroup_id': 339558086, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-美女上车-询价-销量询价（有热区）-1126-亦复-双出价-下单-优先拿量-31_01', 'bid_amount': 2522, 'daily_budget': 0}, {'campaign_id': 165970853, 'adgroup_id': 339557302, 'ad

total_page:  1
{'data': {'list': [{'campaign_id': 171072441, 'adgroup_id': 362378295, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-人群包-动态创意-图片-询价-销量询价（分裂式）-0104-亦复-双出价-下单-优先拿量-222', 'bid_amount': 2688, 'daily_budget': 0}, {'campaign_id': 171072441, 'adgroup_id': 362377946, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-人群包-动态创意-图片-询价-销量询价（分裂式）-0104-亦复-双出价-下单-优先拿量', 'bid_amount': 2522, 'daily_budget': 0}, {'campaign_id': 171072441, 'adgroup_id': 359891233, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-人群包-动态创意-图片-询价-销量询价（车型直降）-1230-亦复-双出价-下单-优先拿量', 'bid_amount': 3122, 'daily_budget': 0}, {'campaign_id': 171719042, 'adgroup_id': 353647516, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-人群包-动态创意-图片-询价-销量询价（车型直降）-1218-亦复-双出价-下单-优先拿量-88_04', 'bid_amount': 3122, 'daily_budget': 0}, {'campaign_id': 171719042, 'adgroup_id': 353647515, 'adgroup_name': '报价安卓-c66-XQ图片1280x720-人群包-动态创意-图片-询价-销量询价（车型直降）-1218-亦复-双出价-下单-优先拿量-88_03', 'bid_amount': 3122, 'daily_budget': 0}, {'campaign_id': 171719042, 'adgroup_id': 353647514, 'adgr

{'data': {'list': [{'campaign_id': 171908910, 'adgroup_id': 354090393, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-情景11-询价-销量询价（分裂）-1220-亦复-双出价-下单-优先拿量-129_01', 'bid_amount': 3125, 'daily_budget': 0}, {'campaign_id': 171908910, 'adgroup_id': 354090101, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-情景11-询价-销量询价（分裂）-1220-亦复-双出价-下单-优先拿量-129', 'bid_amount': 3125, 'daily_budget': 0}, {'campaign_id': 171719193, 'adgroup_id': 353647814, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-情景11-询价-销量询价（分裂）-1220-亦复-双出价-下单-优先拿量-1209_04', 'bid_amount': 3125, 'daily_budget': 0}, {'campaign_id': 171719193, 'adgroup_id': 353647813, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-情景11-询价-销量询价（分裂）-1220-亦复-双出价-下单-优先拿量-1209_03', 'bid_amount': 3125, 'daily_budget': 0}, {'campaign_id': 171719193, 'adgroup_id': 353647812, 'adgroup_name': '报价安卓-c66-XQ视频1280x720-男通投-动态创意-情景11-询价-销量询价（分裂）-1220-亦复-双出价-下单-优先拿量-1209_02', 'bid_amount': 3125, 'daily_budget': 0}, {'campaign_id': 171719193, 'adgroup_id': 353647811,

In [61]:
bjapp_bid_df = pd.read_csv('tencent_gdt_bjapp_bid_2021-02-19.csv', sep='\t')

In [50]:
bjapp_bid_df.shape

(44588, 8)

In [62]:
bjapp_bid_df.head()

campaign_id  adgroup_id                             adgroup_name bid_amount  \
0  3055749862  3055749883  品众-c250-合并组图-标签分析-CS75-文案-实惠好车-0217-单出价       2560   
1  3055746914  3055746924      品众-c250-合并组图-标签多-雅阁-文案-询底价-0217-单出价       2720   
2  3055743013  3055743045   品众-c250-合并大图-标签分析-白色降价榜-通用-0217-单出价-动态       2730   
3  3055736610  3055736623    品众-c250-合并组图-标签分析-RAV4-文案-通用-0217-单出价       2220   
4  3055732825  3055732831     品众-c250-合并组图-标签多-卡罗拉-文案-浮层卡-0217-单出价       2690   

  daily_budget          account_name account_id          dt  
0            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
1            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
2            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
3            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
4            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19

In [63]:
bjapp_bid_df = bjapp_bid_df.loc[bjapp_bid_df.campaign_id!='campaign_id', :].drop_duplicates()

In [64]:
bjapp_bid_df['bid_amount'] = bjapp_bid_df.bid_amount.map(lambda x: round(int(x)/100, 2))

In [65]:
bjapp_bid_df.head()

campaign_id  adgroup_id                             adgroup_name  \
0  3055749862  3055749883  品众-c250-合并组图-标签分析-CS75-文案-实惠好车-0217-单出价   
1  3055746914  3055746924      品众-c250-合并组图-标签多-雅阁-文案-询底价-0217-单出价   
2  3055743013  3055743045   品众-c250-合并大图-标签分析-白色降价榜-通用-0217-单出价-动态   
3  3055736610  3055736623    品众-c250-合并组图-标签分析-RAV4-文案-通用-0217-单出价   
4  3055732825  3055732831     品众-c250-合并组图-标签多-卡罗拉-文案-浮层卡-0217-单出价   

   bid_amount daily_budget          account_name account_id          dt  
0        25.6            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
1        27.2            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
2        27.3            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
3        22.2            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19  
4        26.9            0  广点通_安卓_品众3(15128620)   15128620  2021-02-19

# --------------------------------------------------------

# 整合搜索oCPC消费报告

In [17]:
# pcwap_ocpc_cost = r'C:/Users/jsynl/Desktop/baidu_sem_ocpcbid/data/pcwap_ocpc_cost/'

In [18]:
# os.chdir(pcwap_ocpc_cost)
# matrix = []

# for f in os.listdir(pcwap_ocpc_cost):
#     print(f)
#     df = pd.read_csv(f, skiprows=7, encoding='GB18030')
#     matrix.append(df)
    
# full_df = pd.concat(matrix, ignore_index=True, axis=0)

In [19]:
# full_df.head(2)

In [20]:
# filter_cols = ['日期', '投放包ID', 'OCPC阶段', '开启层级', '目标转化量','深度转化量'
#                ,'消费', '点击', '展现', '目标转化成本', '无效转化过滤量']

In [21]:
# full_df = full_df[filter_cols]

In [22]:
# full_df.head(2)

# 加载 pcwap 消费数据

In [23]:
pcwap_cost_file = os.path.join(conf_path, 'bd_sem_daily_report_{}.csv'.format(datedelta(1)))

In [24]:
pcwap_cost_cols = ['日期', '账户ID', '账户', '推广计划ID', '推广计划', '推广单元ID', '推广单元'
                    ,'关键词keywordID', '关键词ID', '关键词', '展现量', '点击量', '消费', '平均点击价格', '千次展现消费']

In [25]:
pcwap_cost_df = pd.read_csv(pcwap_cost_file, sep='\t', names=pcwap_cost_cols)

In [26]:
pcwap_cost_df.head(2)

日期      账户ID                   账户    推广计划ID     推广计划      推广单元ID  \
0  2020-12-28  19369520  baidu-无线bcH58160182  84845728  商品_一汽红旗  3447479440   
1  2020-12-28  19369520  baidu-无线bcH58160182  84845728  商品_一汽红旗  3447479440   

         推广单元  关键词keywordID       关键词ID                关键词  展现量  点击量     消费  \
0  闪投_一汽红旗_全系   95748987132  4775170723              ~商品定向  177   11  12.47   
1  闪投_一汽红旗_全系   96207003982  4887625166  #thirdcategory#报价  512   35  27.00   

   平均点击价格  千次展现消费  
0    1.13   70.45  
1    0.77   52.73

In [27]:
aggr_pcwap_cost = pcwap_cost_df.groupby(['日期','账户ID','账户','推广计划ID','推广计划'])[['展现量','点击量','消费']].sum().reset_index()

In [28]:
aggr_pcwap_cost.head()

日期      账户ID                   账户    推广计划ID     推广计划     展现量  \
0  2020-12-28  19369520  baidu-无线bcH58160182  84845728  商品_一汽红旗    2156   
1  2020-12-28  19369520  baidu-无线bcH58160182  89151254  商品_东风日产   20496   
2  2020-12-28  19369520  baidu-无线bcH58160182  89160651    商品_奥迪    4921   
3  2020-12-28  19369520  baidu-无线bcH58160182  89516385  商品_华晨宝马  103999   
4  2020-12-28  19369520  baidu-无线bcH58160182  89602244  商品_长城汽车   21604   

     点击量        消费  
0    253    173.79  
1   1906   1977.63  
2    475    823.84  
3  12773  15057.08  
4   2366   2515.34

# 加载 pcwap 投放包与计划对应维表

In [29]:
pcwap_dim_file = os.path.join(conf_path, 'dim_pcwap_planid_package_map.xlsx')

In [30]:
pcwap_dim_df = pd.read_excel(pcwap_dim_file)

In [31]:
pcwap_dim_df.head()

accountName   planName ocpcPackage
0  baidu-无线bcH58160182   商品_全商品计划         全品牌
1  baidu-无线bcH58160182  商品_比亚迪新能源      比亚迪新能源
2  baidu-无线bcH58160182     商品_斯巴鲁         小品牌
3  baidu-无线bcH58160182    商品_威马汽车        威马汽车
4  baidu-无线bcH58160182    商品_零跑汽车        零跑汽车

In [32]:
pcwap_plan_cost = aggr_pcwap_cost.merge(pcwap_dim_df, left_on=['账户','推广计划'], right_on=['accountName','planName'])

In [33]:
# 筛选昨天得消费数据

pcwap_plan_cost = pcwap_plan_cost[pcwap_plan_cost['日期']==datedelta(1)]

In [34]:
pcwap_plan_cost.head()

日期      账户ID                   账户    推广计划ID     推广计划    展现量   点击量  \
6   2021-01-03  19369520  baidu-无线bcH58160182  84845728  商品_一汽红旗   1340   218   
13  2021-01-03  19369520  baidu-无线bcH58160182  89151254  商品_东风日产  26058  2400   
20  2021-01-03  19369520  baidu-无线bcH58160182  89160651    商品_奥迪  10723  1066   
27  2021-01-03  19369520  baidu-无线bcH58160182  89516385  商品_华晨宝马  65275  7160   
34  2021-01-03  19369520  baidu-无线bcH58160182  89602244  商品_长城汽车  19541  2051   

         消费          accountName planName ocpcPackage  
6    202.16  baidu-无线bcH58160182  商品_一汽红旗    闪投_一汽红旗移  
13  2527.53  baidu-无线bcH58160182  商品_东风日产     闪投_东风日产  
20  1131.81  baidu-无线bcH58160182    商品_奥迪     闪投_奥迪-重  
27  7011.92  baidu-无线bcH58160182  商品_华晨宝马   闪投_华晨宝马-重  
34  1719.57  baidu-无线bcH58160182  商品_长城汽车     闪投_长城汽车

# 加载搜索出价报告

In [35]:
pcwap_bid_rpt = os.path.join(data_path, 'baidu_sem_pcwap_ocpcbid_{}.xlsx'.format(datedelta(0)))

In [36]:
pcwap_bid = pd.read_excel(pcwap_bid_rpt)

In [37]:
pcwap_bid.head(2)

投放包id 投放包名称  出价类型(1: ocpc 2: ecpc)  优化的设备类型(1: PC 2: 移动)  \
0  341625619  东风标致                      1                     2   
1  325945598  英菲尼迪                      1                     2   

   目标转化成本 (元/转化)  eCPC最大议价系数  eCPC最小议价系数  投放阶段  \
0           80.0          -1          -1     2   
1           80.0          -1          -1     2   

                                                生效范围                 账户名称  \
0                [{'levelId': 90163211, 'level': 2}]  baidu-无线bcH58160182   
1  [{'levelId': 93198968, 'level': 2}, {'levelId'...  baidu-无线bcH58160182   

       账户id   平台类型          日期  
0  19369520  pcwap  2021-01-04  
1  19369520  pcwap  2021-01-04

In [38]:
pcwap_bid = pcwap_bid[['投放包id', '投放包名称', '出价类型(1: ocpc 2: ecpc)' 
                       ,'目标转化成本 (元/转化)', '账户名称', '账户id', '平台类型', '日期']]

# 整合并产出搜索出价日报

In [39]:
merge_df = pcwap_bid.merge(pcwap_plan_cost, left_on=['账户名称','投放包名称'], right_on=['账户','ocpcPackage'], suffixes=('_x', '_y'))
# merge_df.head(2)

merge_cols = ['投放包id', '投放包名称', '出价类型(1: ocpc 2: ecpc)', '目标转化成本 (元/转化)', '账户名称',
              '账户id', '平台类型', '日期_x', '日期_y', '推广计划ID', '推广计划', '展现量', '点击量', '消费']

final_cols = ['投放包id', '投放包名称', '出价类型(1: ocpc 2: ecpc)', 'oCPC出价 (元/转化)', '账户名称',
              '账户id', '平台类型', '出价日期', '消费日期', '推广计划ID', '推广计划', '展现量', '点击量', '消费']

merge_df = merge_df[merge_cols]
merge_df.columns = final_cols

merge_df.to_excel(os.path.join(data_path, '百度搜索PCWAP出价日报_{}.xlsx'.format(datedelta(0))), index=None)

# --------------------------------------------------------

# 整合报价oCPC消费报告

In [42]:
# bjapp_ocpc_cost = r'C:/Users/jsynl/Desktop/baidu_sem_ocpcbid/data/bjapp_ocpc_cost/'

In [43]:
# os.chdir(bjapp_ocpc_cost)
# matrix = []

# for f in os.listdir(bjapp_ocpc_cost):
#     print(f)
#     df = pd.read_csv(f, skiprows=7, encoding='GB18030')
#     matrix.append(df)
    
# bjfull_df = pd.concat(matrix, ignore_index=True, axis=0)

In [44]:
# bjfull_df.head(2)

In [45]:
# bjfilter_cols = ['日期', '投放包ID', 'OCPC阶段', '开启层级', '目标转化量','深度转化量'
#                  ,'消费', '点击', '展现', '目标转化成本', '无效转化过滤量']

In [46]:
# bjfull_df = bjfull_df[bjfilter_cols]

In [47]:
# bjfull_df.head(2)

# 加载 bjapp 消费报告

In [95]:
bjapp_cost_file = os.path.join(data_path, 'gdt-{}-创意日报.xlsx'.format(datedelta(2)))

In [96]:
bjapp_cost_df = pd.read_excel(bjapp_cost_file)

In [97]:
bjapp_cost_df.head(2)

日期     平台  渠道ID      账户名称       计划ID  \
0  2021-02-10  10004  c250  15128620  176858518   
1  2021-02-10  10004  c250  15128620  177319926   

                                       计划名称       单元ID  \
0  品众-c250-合并大图-标签分析-区间降价榜3-查底价-0113-双出价-下单  367370470   
1      品众-c250-合并大图-买车-黄色降价榜-文案-通用-0115-双出价  368729552   

                                            单元  创意名称/关键词ID  \
0  品众-c250-合并大图-标签分析-区间降价榜3-文案-查底价-0113-双出价-下单   462371817   
1         品众-c250-合并大图-买车-黄色降价榜-文案-通用-0115-双出价   464236425   

                        创意名称/关键词  ...  下载量  激活量  当日激活线索  当日激活用户      激活量成本  \
0          动态创意_20210113143248_1  ...    0  0.0     0.0     0.0        NaN   
1  创意8-2020-12-29 17:06:33_复制_复制  ...    2  1.0     0.0     0.0  19.395393   

   当日激活线索成本  当日激活用户成本  线索转化率  用户转化率  是否匹配上  
0       NaN       NaN    NaN    NaN      是  
1       NaN       NaN    NaN    NaN      是  

[2 rows x 25 columns]

In [98]:
aggr_bjapp_cost = bjapp_cost_df.groupby(['日期','账户名称','计划ID','计划名称','单元ID'])[['展示数','点击数','消费','现金','下载量','激活量']].sum().reset_index()

In [99]:
aggr_bjapp_cost

日期      账户名称        计划ID  \
0     2021-02-10  14731425   168387922   
1     2021-02-10  14731425   171989455   
2     2021-02-10  14731425   173192508   
3     2021-02-10  14731425   173362387   
4     2021-02-10  14731425   173823441   
...          ...       ...         ...   
2001  2021-02-12  17843219   176988512   
2002  2021-02-12  17843219  3010917581   
2003  2021-02-12  17843219  3020918295   
2004  2021-02-12  17843219  3021181000   
2005  2021-02-12  17843219  3021300828   

                                           计划名称        单元ID    展示数  点击数  \
0                微盟-c222-XQXS大图-动态-下单双目标-1207-1   360348598    197    5   
1        微盟-c222-XQXS大图-汽_交通大类-动态-下单双目标-1220-01   354289985      3    0   
2          微盟-c222-XQXS大图-系统优选-动态-下单双目标-1225-02   357381638   2515   30   
3          微盟-c222-XQXS大图-系统优选-动态-下单双目标-1227-01   357913972    672    3   
4        微盟-c222-XQXS大图-汽_大类定向-动态-下单双目标-1229-01   359099076  28926  456   
...                                         ...         ...    ...  ...   
2001     亦复-c66-0113-ZN图片1280x720-安卓-OCPM-图片-销量   367767885   9505  104   
2002   亦复-c66-0129-XQ视频1280x720-安卓-OCPM-测试-销量-4  3010917675      0    0   
2003    亦复-c66-0202-ZN图片1280x720-安卓-OCPM-图片2-销量  3020918371  33637  581   
2004  亦复-c66-0202-ZN图片1280x720-安卓-OCPM-图片2-销量-2  3021181093   2847   49   
2005  亦复-c66-0202-ZN图片1280x720-安卓-OCPM-跑的好的素材-3  3021300859    824   25   

          消费          现金  下载量   激活量  
0       4.24    4.198020    0   0.0  
1       0.00    0.000000    0   0.0  
2      55.03   54.485149    4   1.0  
3       6.16    6.099010    0   0.0  
4     313.15  310.049505   45  17.0  
...      ...         ...  ...   ...  
2001   52.43   51.151220   10   4.0  
2002    0.00    0.000000    0   0.0  
2003  283.33  276.419512   20   8.0  
2004   19.37   18.897561    0   0.0  
2005    9.29    9.063415    0   0.0  

[2006 rows x 11 columns]

In [100]:
aggr_bjapp_cost.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2006 entries, 0 to 2005
Data columns (total 11 columns):
日期      2006 non-null object
账户名称    2006 non-null int64
计划ID    2006 non-null int64
计划名称    2006 non-null object
单元ID    2006 non-null int64
展示数     2006 non-null int64
点击数     2006 non-null int64
消费      2006 non-null float64
现金      2006 non-null float64
下载量     2006 non-null int64
激活量     2006 non-null float64
dtypes: float64(3), int64(6), object(2)
memory usage: 172.5+ KB


In [102]:
# 获取昨天消费数据

aggr_bjapp_cost = aggr_bjapp_cost.loc[aggr_bjapp_cost['日期']==datedelta(8), :]

In [103]:
aggr_bjapp_cost

日期      账户名称        计划ID  \
1365  2021-02-12  14731425   168387922   
1366  2021-02-12  14731425   171989455   
1367  2021-02-12  14731425   173192508   
1368  2021-02-12  14731425   173362387   
1369  2021-02-12  14731425   173823441   
...          ...       ...         ...   
2001  2021-02-12  17843219   176988512   
2002  2021-02-12  17843219  3010917581   
2003  2021-02-12  17843219  3020918295   
2004  2021-02-12  17843219  3021181000   
2005  2021-02-12  17843219  3021300828   

                                           计划名称        单元ID    展示数  点击数  \
1365             微盟-c222-XQXS大图-动态-下单双目标-1207-1   360348598    229    6   
1366     微盟-c222-XQXS大图-汽_交通大类-动态-下单双目标-1220-01   354289985      0    0   
1367       微盟-c222-XQXS大图-系统优选-动态-下单双目标-1225-02   357381638    814    9   
1368       微盟-c222-XQXS大图-系统优选-动态-下单双目标-1227-01   357913972    453    5   
1369     微盟-c222-XQXS大图-汽_大类定向-动态-下单双目标-1229-01   359099076  32517  580   
...                                         ...         ...    ...  ...   
2001     亦复-c66-0113-ZN图片1280x720-安卓-OCPM-图片-销量   367767885   9505  104   
2002   亦复-c66-0129-XQ视频1280x720-安卓-OCPM-测试-销量-4  3010917675      0    0   
2003    亦复-c66-0202-ZN图片1280x720-安卓-OCPM-图片2-销量  3020918371  33637  581   
2004  亦复-c66-0202-ZN图片1280x720-安卓-OCPM-图片2-销量-2  3021181093   2847   49   
2005  亦复-c66-0202-ZN图片1280x720-安卓-OCPM-跑的好的素材-3  3021300859    824   25   

          消费          现金  下载量   激活量  
1365    2.23    2.207921    0   0.0  
1366    0.00    0.000000    0   0.0  
1367   14.28   14.138614    0   0.0  
1368    6.02    5.960396    1   1.0  
1369  313.96  310.851485   49  13.0  
...      ...         ...  ...   ...  
2001   52.43   51.151220   10   4.0  
2002    0.00    0.000000    0   0.0  
2003  283.33  276.419512   20   8.0  
2004   19.37   18.897561    0   0.0  
2005    9.29    9.063415    0   0.0  

[641 rows x 11 columns]

# 加载 bjapp 出价报告

In [104]:
bjapp_bid_df.head()

campaign_id  adgroup_id                             adgroup_name  \
0   3055749862  3055749883  品众-c250-合并组图-标签分析-CS75-文案-实惠好车-0217-单出价   
1   3055746914  3055746924      品众-c250-合并组图-标签多-雅阁-文案-询底价-0217-单出价   
2   3055743013  3055743045   品众-c250-合并大图-标签分析-白色降价榜-通用-0217-单出价-动态   
3   3055736610  3055736623    品众-c250-合并组图-标签分析-RAV4-文案-通用-0217-单出价   
4   3055732825  3055732831     品众-c250-合并组图-标签多-卡罗拉-文案-浮层卡-0217-单出价   

   bid_amount daily_budget          account_name  account_id          dt  
0        25.6            0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  
1        27.2            0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  
2        27.3            0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  
3        22.2            0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  
4        26.9            0  广点通_安卓_品众3(15128620)    15128620  2021-02-19

In [105]:
bjapp_bid_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 44130 entries, 0 to 44587
Data columns (total 8 columns):
campaign_id     44130 non-null int64
adgroup_id      44130 non-null int64
adgroup_name    44130 non-null object
bid_amount      44130 non-null float64
daily_budget    44130 non-null object
account_name    44130 non-null object
account_id      44130 non-null int64
dt              44130 non-null object
dtypes: float64(1), int64(3), object(4)
memory usage: 3.0+ MB


In [106]:
for col in bjapp_bid_df.columns:
    if col in ['campaign_id','adgroup_id','account_id']:
        bjapp_bid_df[col] = bjapp_bid_df[col].astype('int64')
    else:
        continue

In [107]:
bjapp_bid_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 44130 entries, 0 to 44587
Data columns (total 8 columns):
campaign_id     44130 non-null int64
adgroup_id      44130 non-null int64
adgroup_name    44130 non-null object
bid_amount      44130 non-null float64
daily_budget    44130 non-null object
account_name    44130 non-null object
account_id      44130 non-null int64
dt              44130 non-null object
dtypes: float64(1), int64(3), object(4)
memory usage: 3.0+ MB


# 整合并产出报价出价日报

In [108]:
bjapp_bid_df.merge(aggr_bjapp_cost, left_on=['account_id','campaign_id','adgroup_id'], right_on=['账户名称','计划ID','单元ID'], suffixes=('_x', '_y'))

campaign_id  adgroup_id  \
0     3037581101  3037581128   
1     3037581101  3037581128   
2     3037576187  3037576213   
3     3037576187  3037576213   
4     3037530763  3037530791   
..           ...         ...   
714    171580905   353288709   
715    170981427   351743467   
716    167171658   342434222   
717    166557715   340932774   
718    163080571   334218284   

                                          adgroup_name  bid_amount  \
0                品众-c250-合并大图-系统优选-汉兰达-文案-浮层卡-0207-双出价       19.60   
1                品众-c250-合并大图-系统优选-汉兰达-文案-浮层卡-0207-双出价       19.60   
2                品众-c250-合并大图-标签分析-汉兰达-文案-浮层卡-0207-双出价       19.70   
3                品众-c250-合并大图-标签分析-汉兰达-文案-浮层卡-0207-双出价       19.70   
4                品众-c250-合并大图-标签分析-途观L-文案-浮层卡-0207-单出价       19.40   
..                                                 ...         ...   
714  报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-...       26.14   
715  报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-...       26.54   
716  报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-...       26.54   
717  报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-...       26.55   
718  报价安卓-c66-XQ图片1280*720-罗卡-常规创意-图片-询价-销量询价（有热区）-...       24.23   

    daily_budget          account_name  account_id          dt          日期  \
0              0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  2021-02-12   
1              0  广点通_安卓_品众3(15128620)    15128620  2021-02-20  2021-02-12   
2              0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  2021-02-12   
3              0  广点通_安卓_品众3(15128620)    15128620  2021-02-20  2021-02-12   
4              0  广点通_安卓_品众3(15128620)    15128620  2021-02-19  2021-02-12   
..           ...                   ...         ...         ...         ...   
714            0  广点通_安卓_亦复8(17843193)    17843193  2021-02-20  2021-02-12   
715            0  广点通_安卓_亦复8(17843193)    17843193  2021-02-20  2021-02-12   
716            0  广点通_安卓_亦复8(17843193)    17843193  2021-02-20  2021-02-12   
717            0  广点通_安卓_亦复8(17843193)    17843193  2021-02-20  2021-02-12   
718            0  广点通_安卓_亦复8(17843193)    17843193  2021-02-20  2021-02-12   

         账户名称        计划ID                                     计划名称  \
0    15128620  3037581101    品众-c250-合并大图-系统优选-汉兰达-文案-浮层卡-0207-双出价   
1    15128620  3037581101    品众-c250-合并大图-系统优选-汉兰达-文案-浮层卡-0207-双出价   
2    15128620  3037576187    品众-c250-合并大图-标签分析-汉兰达-文案-浮层卡-0207-双出价   
3    15128620  3037576187    品众-c250-合并大图-标签分析-汉兰达-文案-浮层卡-0207-双出价   
4    15128620  3037530763     品众-c250-合并大图-标签分析-探岳-文案-浮层卡-0207-单出价   
..        ...         ...                                      ...   
714  17843193   171580905  亦复-c66-1218-XQ图片1280*720-安卓-OCPM-图片-销量6   
715  17843193   170981427  亦复-c66-1217-XQ图片1280*720-安卓-OCPM-图片-销量5   
716  17843193   167171658   亦复-c66-1205-XQ图片1280*720-安卓-OCPM-图片-销量   
717  17843193   166557715   亦复-c66-1201-XQ图片1280*720-安卓-OCPM-图片-销量   
718  17843193   163080571   亦复-c66-1118-XQ图片1280*720-安卓-OCPM-图片-销量   

           单元ID    展示数  点击数      消费          现金  下载量  激活量  
0    3037581128    269    0    6.12    5.873321    0  0.0  
1    3037581128    269    0    6.12    5.873321    0  0.0  
2    3037576213   3651   23   38.73   37.168906    4  1.0  
3    3037576213   3651   23   38.73   37.168906    4  1.0  
4    3037530791    145    0    3.12    2.994242    0  0.0  
..          ...    ...  ...     ...         ...  ...  ...  
714   353288709      0    0    0.00    0.000000    0  0.0  
715   351743467      0    0    0.00    0.000000    0  0.0  
716   342434222      0    0    0.00    0.000000    0  0.0  
717   340932774  14572  337  110.33  107.639024   13  5.0  
718   334218284   2284   37   21.45   20.926829    0  0.0  

[719 rows x 19 columns]

In [110]:
bjapp_merge_df = bjapp_bid_df.merge(aggr_bjapp_cost, left_on=['account_id','campaign_id','adgroup_id'], right_on=['账户名称','计划ID','单元ID'], suffixes=('_x', '_y'))
# merge_df.head(2)

bjapp_merge_cols = ['account_name','account_id','campaign_id','adgroup_id','adgroup_name','bid_amount','daily_budget','dt'
                    ,'日期','展示数','点击数','消费','现金','下载量','激活量']

final_cols = ['账户名称','账户ID','计划ID','单元ID','单元名称','出价','日预算','出价日期'
              ,'消费日期','展示数','点击数','消费','现金','下载量','激活量']

bjapp_merge_df = bjapp_merge_df[bjapp_merge_cols]
bjapp_merge_df.columns = final_cols

bjapp_merge_df.to_excel(os.path.join(data_path, '腾讯广点通BJAPP出价日报_{}.xlsx'.format(datedelta(0))), index=None)